In [5]:
import sys
import numpy as np
import cProfile
import matplotlib.pyplot as plt
import scipy.optimize
import functools
from functools import partial
from bokeh.plotting import figure, show, output_notebook
import bokeh
import datashader as ds
from datashader import transfer_functions as tf
from datashader.utils import export_image
from datashader.bokeh_ext import InteractiveImage
from datashader.colors import colormap_select, Greys9, Hot, viridis, inferno
from IPython.core.display import HTML, display
import pandas as pd


In [6]:
def seta(avalue):
    """
    In order for the rest of these functions to use the a and b values 
    that I want they must be set inside here.  This function sets the 
    value of a.  Similarly with setb
    """
    global a
    a = float(avalue)
    print('a has been set to:',a)
    return

def setb(bvalue):
    """
    See seta
    """
    global b 
    b = float(bvalue)
    print('b has been set to:',b)
    return

def Map(z):
    """
    Takes in an array points and iterates them with the SNTM.  
    Must be numpy array. This does not mod.
    NOTE: This changes what is passed. 
    The points should be in shape [[x0,y0],[x1,y1],[x2,y2]]
    init.shape = (n,2) where n is the number of points.
    This will work with only one point as well, however,
    currently it must still be a numpy array.
    """
    z[:,1] = z[:,1] - b*np.sin(2*np.pi*z[:,0])
    z[:,0] = (z[:,0] + a*(1-z[:,1]**2))
    return z

In [7]:
def xcoord(z):
    """
    returns the x component of the orbit
    """
    return z[:,0]

def ycoord(z):
    """
    returns the y component of the orbit
    """
    return z[:,1]

def zeroY(y):
    """
    Used in function composition to plug in an array with zero intial x 
    and arbitrary y.
    """
    return np.array([[0,y]])

def compose(functions):
    """
    Defined recursively.  Provide a tuple of function names and this returns 
    a function which is their composition. For more information look here:
    https://mathieularose.com/function-composition-in-python/
    """
    return functools.reduce(lambda f,g: lambda x: f(g(x)),functions, lambda x: x)

In [8]:
def orbit(initialConditions, orbitLength):
    """
    Takes array of shape (n,2) of n initial conditions and returns an
    array of shape (n,2,orbitLength) such that the orbit goes from 0 
    to orbitLength.  This means if it is a periodic orbit of length equal
    to the orbitLength the first and last entry should be the same

    NOTE: For index purposes: 
    The first index corresponds to the index of the initial condition.  
    The second index chooses x or y 
    The third index is the position on the orbit
    """
    initCondLength= len(initialConditions[:,0])
    orbit = np.zeros((initCondLength,2,orbitLength+1),dtype='float64')
    orbit[:,:,0]=initialConditions
    print('Calculating orbits using SNTM....')
    print('There are',initCondLength,'orbits of length', orbitLength)
    for i in range(orbitLength):
        if i%1000 == 0:
            print('finished with:',i)
        orbit[:,:,i+1]=orbit[:,:,i]
        Map(orbit[:,:,i+1])
    print('Orbits calculated.')
    return orbit

In [26]:
%%time
seta(.615)
setb(.4)
initconds = np.random.rand(int(2e4),2)-.5
orbitarray = orbit(initconds,int(5e3))

a has been set to: 0.615
b has been set to: 0.4
Calculating orbits using SNTM....
There are 20000 orbits of length 5000
finished with: 0
finished with: 1000
finished with: 2000
finished with: 3000
finished with: 4000
Orbits calculated.
CPU times: user 59 s, sys: 2.2 s, total: 1min 1s
Wall time: 1min 1s


In [ ]:
%%time
points = np.array([[],[]])
print('putting the orbits into arrays for plotting...')
for i in range(len(orbitarray[:,0,0])):
    points = np.append(points,orbitarray[i,:,:],axis=1)
points[0,:]=points[0,:]%1-.5


df = pd.DataFrame(points.T,columns=['x','y'])
print('finished. Here are the last three rows:\n', df.tail(3))

putting the orbits into arrays for plotting...


In [12]:
output_notebook()

Loading BokehJS ...

In [15]:
def base_plot(tools='pan,wheel_zoom,reset',plot_width=plot_width, plot_height=plot_height, **plot_args):
    p = figure(tools=tools, plot_width=plot_width, plot_height=plot_height,
        x_range=x_range, y_range=y_range, outline_line_color=None,
        min_border=0, min_border_left=0, min_border_right=0,
        min_border_top=0, min_border_bottom=0, **plot_args)
    
    p.axis.visible = True
    p.xgrid.grid_line_color = None
    p.ygrid.grid_line_color = None
    return p

In [23]:
def create_image(x_range,y_range,w=plot_width,h=plot_height):
    cvs = ds.Canvas(plot_width=plot_width,plot_height=plot_height,x_range=x_range, y_range=y_range)
    agg = cvs.points(df,'x','y')
    img = tf.interpolate(agg,cmap=Hot,how='log')
    return tf.dynspread(img,threshold=0.4,max_px=4)

In [21]:
x_range = (-.5,.5)
y_range = (-.5,.5)

maps = x_range, y_range = ((-.5,.5),(-.5,.5))
plot_width = int(900)
plot_height = int(plot_width//1.6)

background = "black"
export = partial(export_image, export_path="export", background=background)

In [24]:
cm = partial(colormap_select, reverse=(background=="black"))
p=base_plot(background_fill_color=background)
export(create_image(*maps),'testexport')
InteractiveImage(p,create_image)